In [1]:
import requests
import zipfile
import io
import pandas as pd

# UMLS metasaurus downloader: 

download in windows

Download the first part needed for QuickUMLS: mrconso.zip. Extraction is down manually after downloading.

In [9]:
from umls_downloader import download_umls

API_KEY = "15d51489-441e-4e75-bfe5-f1a84c7cea10"
# Replace "<your API key>" with your actual UMLS API key


Testing the api key

In [11]:
import requests

test_url = f"https://uts-ws.nlm.nih.gov/download?url=https://download.nlm.nih.gov/umls/kss/2025AA/umls-2025AA-mrsty.zip&apiKey={API_KEY}"

r = requests.head(test_url)
print("Status code:", r.status_code)
if r.status_code == 200:
    print("✅ API key works, file should be downloadable")
else:
    print("❌ API key failed or access denied")

Status code: 200
✅ API key works, file should be downloadable


Manually download what quickUMLS needs

Download the entire metasaurus, which includes the 2 keys files needed for quickUMLS: MRCONSO.RRF and MRSTY.RRF. WE then extract the zip separately extract size is 35 GB unextracted is around 5GB



In [ ]:
from umls_downloader import open_umls_full

# Make sure your API key is stored in an environment variable or passed as an argument
# we can focus oon particular files or not
try:
    with open_umls_full(name="MRSTY.RRF", api_key=API_KEY) as mrsty_file:
        for line in mrsty_file:
            # Process the MRSTY data here
            continue
except Exception as e:
    print(f"An error occurred during download: {e}")

C0000005|T116|A1.4.1.2.1.7|Amino Acid, Peptide, or Protein|AT17648347|256|
C0000005|T121|A1.4.1.1.1|Pharmacologic Substance|AT17575038|256|
C0000005|T130|A1.4.1.1.4|Indicator, Reagent, or Diagnostic Aid|AT17634323|256|
C0000039|T109|A1.4.1.2.1|Organic Chemical|AT45562015|256|
C0000039|T121|A1.4.1.1.1|Pharmacologic Substance|AT17567371|256|
C0000052|T116|A1.4.1.2.1.7|Amino Acid, Peptide, or Protein|AT08381079|256|
C0000052|T126|A1.4.1.1.3.3|Enzyme|AT08775334|256|
C0000074|T109|A1.4.1.2.1|Organic Chemical|AT205422471|256|
C0000084|T116|A1.4.1.2.1.7|Amino Acid, Peptide, or Protein|AT17641823|256|
C0000084|T123|A1.4.1.1.3|Biologically Active Substance|AT17597318|256|
C0000096|T109|A1.4.1.2.1|Organic Chemical|AT17685682|256|
C0000096|T121|A1.4.1.1.1|Pharmacologic Substance|AT17567369|256|
C0000097|T109|A1.4.1.2.1|Organic Chemical|AT17685735|256|
C0000097|T131|A1.4.1.1.5|Hazardous or Poisonous Substance|AT17619208|256|
C0000098|T109|A1.4.1.2.1|Organic Chemical|AT17696093|256|
C0000098|T131|A

KeyboardInterrupt: 

: 

Downloaded paths are:

"C:\Users\maxji\.data\bio\umls\2025AA\umls-2025AA-metathesaurus-full\2025AA\META\MRSTY.RRF"

"C:\Users\maxji\.data\bio\umls\2025AA\umls-2025AA-metathesaurus-full\2025AA\META\MRCONSO.RRF"

in directory 

C:\Users\maxji\.data\bio\umls\2025AA\umls-2025AA-metathesaurus-full\2025AA\META

Install directory should be for quickUMLS, C:\Users\maxji\.data\bio\quickUMLS



# Building quickumls setup

We will install quickumls on wsl. Therefore, before using quickumls, wsl must be booted. Open vs code using wsl and open this file using the wsl. The same files saved in windows are accessed but we can now use the working wsl environment (since installing quickumls in windows is too hard due to c++ conflicts)
Note that the WSL and Remote Development extensions are key

Then the command for installation is

python -m quickumls.install C:\Users\maxji\.data\bio\umls\2025AA\umls-2025AA-metathesaurus-full\2025AA\META C:\Users\maxji\.data\bio\quickUMLS --database-backend unqlite

Since we are using wsl (for lack of conflicts) we change to 

python -m quickumls.install \
    "/mnt/c/Users/maxji/.data/bio/umls/2025AA/umls-2025AA-metathesaurus-full/2025AA/META" \
    "/mnt/c/Users/maxji/.data/bio/quickUMLS" \
    --database-backend unqlite

# Test code after setup, data format

This code can be used to run on mass data

In [2]:
from quickumls import QuickUMLS


Initializing the starting code the database takes a while to initialize (10)

In [3]:
from quickumls import QuickUMLS
quickumls_db = "/mnt/c/Users/maxji/.data/bio/quickUMLS"

matcher = QuickUMLS(
    quickumls_db,
    threshold=0.7,
    similarity_name='jaccard'
)



However, matching is faster

In [ ]:
text = "The patient was given aspirin for pain relief."
matches = matcher.match(text, best_match=True, ignore_syntax=False)
for x in matches:
    #output all matches
    for final in x:
        print("term:", final["term"])
        semtypes_list = list(final["semtypes"])
        print("semtypes:", semtypes_list) #convert 
        #now, convert semtypes to codes using the dictionary matcher
        semtypes_matches = []
        for type in semtypes_list:
            semtypes_matches.append()
        print(final)

term: pain relief
semtypes: ['T061']
{'start': 34, 'end': 45, 'ngram': 'pain relief', 'term': 'pain relief', 'cui': 'C0451615', 'similarity': 1.0, 'semtypes': {'T061'}, 'preferred': 1}
term: given
semtypes: ['T170']
{'start': 16, 'end': 21, 'ngram': 'given', 'term': 'given', 'cui': 'C3244317', 'similarity': 1.0, 'semtypes': {'T170'}, 'preferred': 1}
term: Inpatient
semtypes: ['T058']
{'start': 4, 'end': 11, 'ngram': 'patient', 'term': 'Inpatient', 'cui': 'C1555324', 'similarity': 0.7142857142857143, 'semtypes': {'T058'}, 'preferred': 1}
term: diaspirin
semtypes: ['T130', 'T109']
{'start': 22, 'end': 29, 'ngram': 'aspirin', 'term': 'diaspirin', 'cui': 'C0163668', 'similarity': 0.7142857142857143, 'semtypes': {'T130', 'T109'}, 'preferred': 1}
term: aspirin
semtypes: ['T121', 'T109']
{'start': 22, 'end': 29, 'ngram': 'aspirin', 'term': 'aspirin', 'cui': 'C0004057', 'similarity': 1.0, 'semtypes': {'T121', 'T109'}, 'preferred': 0}


In [25]:
text = "is it true that if there was a lack of beds due to the virus, doctors would be less likely to save someone with diabetes, because they would be more likely to die??"
matches = matcher.match(text, best_match=True, ignore_syntax=False)
print(matches)
print("printing out separate objects:\n______________________________________________________\n")
#iterate through json to find the text
for x in matches:
    #output all matches
    for final in x:
        print("term:", final["term"])
        semtypes_list = list(final["semtypes"])
        print("semtypes:", semtypes_list) #convert 
        print(final)

[[{'start': 112, 'end': 120, 'ngram': 'diabetes', 'term': 'diabetes', 'cui': 'C0011860', 'similarity': 1.0, 'semtypes': {'T047'}, 'preferred': 1}, {'start': 112, 'end': 120, 'ngram': 'diabetes', 'term': 'diabetes', 'cui': 'C0011849', 'similarity': 1.0, 'semtypes': {'T047'}, 'preferred': 0}, {'start': 112, 'end': 120, 'ngram': 'diabetes', 'term': 'Diabetes', 'cui': 'C0011847', 'similarity': 0.7142857142857143, 'semtypes': {'T047'}, 'preferred': 0}, {'start': 112, 'end': 120, 'ngram': 'diabetes', 'term': 'Diabetes', 'cui': 'C0011849', 'similarity': 0.7142857142857143, 'semtypes': {'T047'}, 'preferred': 0}], [{'start': 84, 'end': 90, 'ngram': 'likely', 'term': 'likely', 'cui': 'C0332148', 'similarity': 1.0, 'semtypes': {'T033'}, 'preferred': 1}], [{'start': 149, 'end': 155, 'ngram': 'likely', 'term': 'likely', 'cui': 'C0332148', 'similarity': 1.0, 'semtypes': {'T033'}, 'preferred': 1}], [{'start': 55, 'end': 60, 'ngram': 'virus', 'term': 'virus', 'cui': 'C0042769', 'similarity': 1.0, 'sem

### General umls format guide

match a sentence against the UMLS concepts. Let me break it down piece by piece:

In [10]:
[{
    'start': 55,
    'end': 60,
    'ngram': 'virus',
    'term': 'virus',
    'cui': 'C0042769',
    'similarity': 1.0,
    'semtypes': {'T047'},
    'preferred': 1
}]

[{'start': 55,
  'end': 60,
  'ngram': 'virus',
  'term': 'virus',
  'cui': 'C0042769',
  'similarity': 1.0,
  'semtypes': {'T047'},
  'preferred': 1}]

* start	The starting character index of the matched phrase in 
* your sentence (0-based). Here, index 55.
* end	The ending character index of the matched phrase. Here, index 60 (exclusive).
* ngram	The substring from your text that was matched. 'virus' in this case.
* term	The UMLS term that matched. Often the same as ngram.
* cui	Concept Unique Identifier from UMLS. 'C0042769' uniquely identifies “virus”.
* similarity	Similarity score between the text and the UMLS concept. 1.0 means exact match.
* semtypes	UMLS semantic types for the concept. {‘T047’} → “Disease or Syndrome” type code.
* preferred	Indicates if this is the preferred match for that term. 1 = yes, 0 = no.

### Loading the semtype label for each category

We can use the MRSTY.RRF path to do a simple dictionary search, in wsl

In [ ]:

mrsty_path = "/mnt/c/Users/maxji/.data/bio/umls/2025AA/umls-2025AA-metathesaurus-full/2025AA/META/MRSTY.RRF"
def load_semtype_labels(mrsty_path):
    df = pd.read_csv(
        mrsty_path,
        sep='|',
        header=None,
        dtype=str,
        engine='python'
    )
    # Drop the last empty column if present
    if df.shape[1] > 6:
        df = df.iloc[:, :6]

    df.columns = ['CUI', 'TUI', 'STN', 'STY', 'ATUI', 'CVF']
    df = df[['TUI', 'STY']].drop_duplicates()
    return dict(zip(df['TUI'], df['STY']))

# Example usage
semtype_labels = load_semtype_labels(mrsty_path)
print(semtype_labels['T047'])  # Disease or Syndrome


Testing code 

In [16]:
semtype_labels

{'T116': 'Amino Acid, Peptide, or Protein',
 'T121': 'Pharmacologic Substance',
 'T130': 'Indicator, Reagent, or Diagnostic Aid',
 'T109': 'Organic Chemical',
 'T126': 'Enzyme',
 'T123': 'Biologically Active Substance',
 'T131': 'Hazardous or Poisonous Substance',
 'T125': 'Hormone',
 'T114': 'Nucleic Acid, Nucleoside, or Nucleotide',
 'T127': 'Vitamin',
 'T195': 'Antibiotic',
 'T129': 'Immunologic Factor',
 'T024': 'Tissue',
 'T073': 'Manufactured Object',
 'T170': 'Intellectual Product',
 'T029': 'Body Location or Region',
 'T184': 'Sign or Symptom',
 'T033': 'Finding',
 'T191': 'Neoplastic Process',
 'T023': 'Body Part, Organ, or Organ Component',
 'T005': 'Virus',
 'T047': 'Disease or Syndrome',
 'T019': 'Congenital Abnormality',
 'T169': 'Functional Concept',
 'T190': 'Anatomical Abnormality',
 'T037': 'Injury or Poisoning',
 'T185': 'Classification',
 'T018': 'Embryonic Structure',
 'T046': 'Pathologic Function',
 'T101': 'Patient or Disabled Group',
 'T093': 'Health Care Related

There 127

In [17]:

print(semtype_labels['T121'])  # Pharmacologic Substance
print(semtype_labels['T047'])  # Disease or Syndrome

Pharmacologic Substance
Disease or Syndrome
